<a href="https://colab.research.google.com/github/hrry121/Assignments/blob/main/Assignments/BigData/Assignment01_SandeepSir/Assignment01_BDA03.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Day of the week wise sales (for e.g. all Sunday together). Print Sunday Onwards..


In [ ]:
import os       #importing os to set environment variable
def install_java():
  !apt-get install -y openjdk-8-jdk-headless -qq > /dev/null      #install openjdk
  os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"     #set environment variable
  !java -version       #check java version
install_java()

openjdk version "1.8.0_462"
OpenJDK Runtime Environment (build 1.8.0_462-8u462-ga~us1-0ubuntu2~22.04.2-b08)
OpenJDK 64-Bit Server VM (build 25.462-b08, mixed mode)


In [ ]:
!apt-get update
!apt-get install openjdk-8-jdk-headless -qq > /dev/null


Get:1 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:4 https://cli.github.com/packages stable InRelease
Hit:5 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:7 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:11 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [127 kB]
Fetched 384 kB in 2s (247 kB/s)
Reading package lists... Done
W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InRelease' does not seem 

In [ ]:
import pyspark

In [ ]:
from pyspark.sql import SparkSession

In [ ]:
spark = SparkSession.builder.appName('Month_Wise').getOrCreate()

In [ ]:
sc=spark.sparkContext

In [ ]:
rdd1=sc.textFile("/content/sample_data/txn.txt")

In [ ]:
import datetime
from datetime import datetime

In [ ]:
rdd1.count()

50000

In [ ]:
rdd1.getNumPartitions()

2

In [ ]:
for var in rdd1.collect():
  print(var)

00000000,06-26-2011,4007024,040.33,Exercise & Fitness,Cardio Machine Accessories,Clarksville,Tennessee,credit
00000001,05-26-2011,4006742,198.44,Exercise & Fitness,Weightlifting Gloves,Long Beach,California,credit 
00000002,06-01-2011,4009775,005.58,Exercise & Fitness,Weightlifting Machine Accessories,Anaheim,California,credit 
00000003,06-05-2011,4002199,198.19,Gymnastics,Gymnastics Rings,Milwaukee,Wisconsin,credit 
00000004,12-17-2011,4002613,098.81,Team Sports,Field Hockey,Nashville  ,Tennessee,credit 
00000005,02-14-2011,4007591,193.63,Outdoor Recreation,Camping & Backpacking & Hiking,Chicago,Illinois,credit 
00000006,10-28-2011,4002190,027.89,Puzzles,Jigsaw Puzzles,Charleston,South Carolina,credit 
00000007,07-14-2011,4002964,096.01,Outdoor Play Equipment,Sandboxes,Columbus,Ohio,credit 
00000008,01-17-2011,4007361,010.44,Winter Sports,Snowmobiling,Des Moines,Iowa,credit 
00000009,05-17-2011,4004798,152.46,Jumping,Bungee Jumping,St. Petersburg,Florida,credit 
00000010,05-29-2011,40

In [ ]:
format_date="%m-%d-%Y"

In [ ]:
rdd2=rdd1.map(lambda a:(datetime.strptime(a.split(",")[1],format_date).strftime("%w"),datetime.strptime(a.split(",")[1],format_date).strftime("%A"),a.split(",")[3]))

In [ ]:
for var in rdd2.take(2):
  print(var)

('0', 'Sunday', '040.33')
('4', 'Thursday', '198.44')


In [ ]:
kvPairRDD=rdd2.map(lambda a:(a[0]+" "+a[1],float(a[2])))

In [ ]:
for var in kvPairRDD.take(2):
  print(var)

('0 Sunday', 40.33)
('4 Thursday', 198.44)


In [ ]:
total=kvPairRDD.reduceByKey(lambda a,b:a+b)

In [ ]:
for var in total.take(2):
  print(var)

('4 Thursday', 733467.2299999995)
('3 Wednesday', 723996.0300000015)


In [ ]:
sortedRDD=total.sortBy(lambda a:int(a[0].split()[0]))

In [ ]:
for var in sortedRDD.collect():
  print(var)

('0 Sunday', 724925.3199999989)
('1 Monday', 739869.9600000007)
('2 Tuesday', 739776.2200000002)
('3 Wednesday', 723996.0300000015)
('4 Thursday', 733467.2299999995)
('5 Friday', 724732.709999999)
('6 Saturday', 724053.0699999991)


In [ ]:
#Reformat
csv_ouput=sortedRDD.map(lambda a:a[0].split()[1]+","+str(round(a[1])))

In [ ]:
for var in csv_ouput.collect():
  print(var)

Sunday,724925
Monday,739870
Tuesday,739776
Wednesday,723996
Thursday,733467
Friday,724733
Saturday,724053


In [ ]:
csv=csv_ouput.coalesce(1)

In [ ]:
csv.getNumPartitions()

1

In [ ]:
csv.saveAsTextFile("/content/sample_data/Weekly1")